# HiggsTools Tutorial

This tutorial is an ipython notebook. Don't worry if you are unfamiliar, these notebooks are super easy to use. Simple read the comment cells, and execute the code cells as you go through. The output of the code will show up directly beneath every cell.

First of all, we import the python package. If this fails, make sure that the `pip install .` line above didn't throw any errors, and that you are now using the same python that you used to install HiggsTools.

In [ ]:
%load_ext wurlitzer

import Higgs
import Higgs.predictions as HP
import Higgs.bounds as HB

### Exploring the HiggsBounds dataset

Let's first take a look at the content of the HiggsBounds dataset. As a first step we need to actually load the dataset. To do so, please adjust the path to the dataset in the fist line of the next cell.

In [ ]:
bounds = Higgs.Bounds("../data/HB")


This loaded all of the limits found in that folder. Now lets take a look at what is in there.

In [ ]:
allLimits = bounds.limits()

lepLimits = [x for x in allLimits if x.collider() == HP.Collider.LEP]
run1Limits = [x for x in allLimits if x.collider() == HP.Collider.LHC8]
run2Limits = [x for x in allLimits if x.collider() == HP.Collider.LHC13]

print("There are {} limits in HiggsBounds".format(len(allLimits)))
print(
    "{} LEP limits, {} LHC Run-1, and {} LHC Run-2 limtis".format(
        len(lepLimits), len(run1Limits), len(run2Limits)
    )
)


In [ ]:
print("The following limits use the full Run-2 dataset:")
for lim in run2Limits:
    if lim.luminosity() > 130:
        print(lim)


You can check a lot of metadata for every limit. If you want to explore what information is included, try `help(Higgs.bounds.Limit)` or take a look at the [documentation](https://higgsbounds.gitlab.io/higgstools/HiggsBoundsAPI.html).

### Providing Model Input with HiggsPredictions

In [ ]:
pred = Higgs.Predictions()
h = pred.addParticle(HP.BsmParticle("h", "neutral", "even"))
h.setMass(125)


Now lets input a simple model prediction. The previous cell first created a new predictions storage and then added a neutral, CP-even scalar called `"h"` and set its mass to 125GeV. All masses, widths, etc in HiggsTools are always in `GeV`, while cross sections are always in `pb`. 

In many cases it is useful to give input through the effective coupling approximation relative to a SM-like Higgs. For example, we can easily set `h` to have exactly SM-like rates and then compare it the limits in HiggsBounds.

In [ ]:
coups = HP.smLikeEffCouplings
print(coups, "\n")

HP.effectiveCouplingInput(h, coups)

res = bounds(pred)
print(res)

print("the following limits are sensitive (expRatio>1) to a SM Higgs:")
for al in res.appliedLimits:
    if al.expRatio() >= 1:
        print(al)


But you can of course also set individual cross sections and branching ratios (or decay widths). Lets add another particle with some (artificial) predicted properties to our predictions.

In [ ]:
if "H" in pred.particleIds():
    H = pred.particle("H")
else:
    H = pred.addParticle(HP.BsmParticle("H", "neutral"))

H.setTotalWidth(0)  # this resets the BRs if you run this cell multiple times
H.setMass(400)
H.setCxn("LHC13", "HW", 0.5)
H.setNormalizedCxn("LHC13", "ggH", 0.1, reference="SMHiggs")

H.setTotalWidth(0.5)
H.setBr("bb", 0.8)
H.setBr("tautau", 0.2)
print("BR(H->bb)={} before setting decay width".format(H.br("bb")))
H.setDecayWidth("Z", "h", 0.1)
print("BR(H->bb)={} after setting decay widths".format(H.br("bb")))
H.setTotalWidth(1)
print("BR(H->bb)={} after changing total width".format(H.br("bb")))

H.setDecayWidth("h", "h", 0.1)
H.setDecayWidth("Z", "h", 0.3)

print("final BRs")
for b in HP.Decay.__members__:
    if H.br(b) > 0:
        print("BR(H->{})={}".format(b, H.br(b)))
print("BR(H->hh)=", H.br("h", "h"))
print("BR(H->Zh)=", H.br("Z", "h"))


In [ ]:
res = bounds(pred)

print(res)

print("-- the following analyses are sentitive to H --")
for al in res.appliedLimits:
    if "H" in al.contributingParticles() and al.expRatio() > 1:
        print(al)


For completeness, lets also add a charged particle and give it some cross sections.

In [ ]:
if "H+" in pred.particleIds():
    Hp = pred.particle("H+")
else:
    Hp = pred.addParticle(HP.BsmParticle("H+", "single"))

Hp.setMass(300)
Hp.setCxn("LHC13", "Hpmtb", 12)
Hp.setDecayWidth("tb", 0.4)
Hp.setDecayWidth("W", "h", 0.3)


res = bounds(pred)

print(res)

print("-- The following analyses are sentitive to H+ --")
for al in res.appliedLimits:
    if "H+" in al.contributingParticles() and al.expRatio() > 1:
        print(al)


## More Examples

### `H -> hSM hSM`

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd

pred = Higgs.Predictions()

h = pred.addParticle(HP.NeutralScalar("h", cp="even"))
H = pred.addParticle(HP.NeutralScalar("H"))

h.setMass(125.09)
HP.effectiveCouplingInput(h, HP.smLikeEffCouplings)
H.setDecayWidth("h", "h", 1)
H.setCxn("LHC13", "ggH", 1)

masses = np.arange(250, 2001, 10)
results = {}
for m in masses:
    H.setMass(m)
    sm = HP.SMHiggs(m)
    results[m] = [
        l for l in bounds(pred).appliedLimits if "H" in l.contributingParticles()
    ]
limits = list({a.limit() for res in results.values() for a in res})
limits.sort(key=lambda l: str(l.id()))

df = pd.DataFrame({"m": masses}).set_index("m")
for lim in limits:
    df[lim.id()] = pd.Series(
        {m: x.obsRatio() for m, res in results.items() for x in res if x.limit() == lim}
    )


def formatProcess(desc):
    parts = desc.split("->")
    finalState = "".join(parts[-2:]).replace(")(X3", "").replace(")", "")
    if len(finalState) > 20:
        return "comb"
    return finalState


fig, ax = plt.subplots()

for lim in limits:
    ax.plot(
        df.index,
        1 / df[lim.id()],
        ls="-" if lim.experiment() == HP.Experiment.ATLAS else "--",
        label="{} {}".format(lim.reference(), formatProcess(lim.processDesc())),
    )
ax.set_yscale("log")
ax.set_xscale("log")

ax.set_xlabel(r"$m_H$ [GeV]")
ax.set_ylabel(r"$\sigma(pp \to H \to h_{125} h_{125})$ [pb]")

ax.set_xticks([300, 400, 500, 600, 700, 800, 900, 1000, 2000])
ax.set_xticklabels([300, 400, 500, "", "", "", "", 1000, 2000])
ax.grid()
atlaslims = [
    l for l in ax.get_lines() if l.get_linestyle() == "--" or l.get_linestyle() == ":"
]
cmslims = [
    l for l in ax.get_lines() if l.get_linestyle() == "-" or l.get_linestyle() == "-."
]
legend1 = ax.legend(
    atlaslims,
    [l.get_label() for l in atlaslims],
    loc="upper left",
    title="ATLAS $13\,\mathrm{TeV}$",
    bbox_to_anchor=(1.04, 0.95),
)
legend2 = ax.legend(
    cmslims,
    [l.get_label() for l in cmslims],
    loc="upper left",
    title="CMS $13\,\mathrm{TeV}$",
    bbox_to_anchor=(1.65, 0.95),
)
ax.add_artist(legend1)
plt.show()


## 2HDM Example

This example is one of the benchmark planes from [2103.07484](https://arxiv.org/abs/2103.07484).
The datafile is linked on the indico page.

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd

df = pd.read_table("cH_WA.tar.xz")

pred = Higgs.Predictions()

hl = pred.addParticle(HP.BsmParticle("Hl", "neutral", "even"))
hh = pred.addParticle(HP.BsmParticle("Hh", "neutral", "even"))
hA = pred.addParticle(HP.BsmParticle("A", "neutral", "odd"))
Hp = pred.addParticle(HP.BsmParticle("Hp", "single"))


def setPrediction(row):
    hl.setMass(row["mHl"])
    hh.setMass(row["mHh"])
    hA.setMass(row["mA"])
    Hp.setMass(row["mHp"])

    cHl = HP.NeutralEffectiveCouplings(
        tt=row.c_Hluu_e,
        bb=row.c_Hldd_e,
        tautau=row.c_Hlll_e,
        WW=row.c_HlVV,
        ZZ=row.c_HlVV,
    )
    cHh = HP.NeutralEffectiveCouplings(
        tt=row.c_Hhuu_e,
        bb=row.c_Hhdd_e,
        tautau=row.c_Hhll_e,
        WW=row.c_HhVV,
        ZZ=row.c_HhVV,
    )
    cA = HP.NeutralEffectiveCouplings(
        tt=1j * row.c_Auu_o, bb=1j * row.c_Add_o, tautau=1j * row.c_All_o
    )
    for c in (cHl, cHh, cA):
        c.uu = c.tt
        c.cc = c.tt
        c.dd = c.bb
        c.ss = c.bb
        c.gg = np.abs(c.tt)

    HP.effectiveCouplingInput(hl, cHl)
    HP.effectiveCouplingInput(hh, cHh)
    HP.effectiveCouplingInput(hA, cA)

    for h in (hl, hh, hA):
        h.setTotalWidth(0)  # resets all Brs
        h.setTotalWidth(row["w_{}".format(h.id())])
        for d in HP.Decay.__members__:
            brKey = "b_{}_{}".format(h.id(), d)
            if brKey in row.keys():
                h.setBr(d, row[brKey])
        for x in ("ggH", "bbH"):
            h.setCxn("LHC13", x, row["x_{}_{}".format(h.id(), x)])

    hh.setBr("Z","A",row.b_Hh_ZA)
    hl.setBr("Z","A",row.b_Hl_ZA)
    hA.setBr("Z","Hl",row.b_A_ZHl)
    hA.setBr("Z","Hh",row.b_A_ZHh)

    hh.setBr("Hl","Hl",row.b_Hh_HlHl)
    hh.setBr("A","A",row.b_Hh_AA)

    

    for d in HP.Decay.__members__:
        Hp.setTotalWidth(row["w_Hp"])
        brKey = "b_Hp_{}".format(d)
        if brKey in row.keys():
            Hp.setBr(d, row[brKey])
    Hp.setCxn("LHC13", "Hpmtb", row["x_tHpm"])


def applyToPoint(point):
    setPrediction(point)
    return bounds(pred)


df["hbResult"] = df.apply(applyToPoint, axis="columns")


In [ ]:

df["selA"] = [x.selectedLimits["A"].limit().id() for x in df.hbResult]
df["obsRA"] = [x.selectedLimits["A"].obsRatio() for x in df.hbResult]
df["selHh"] = [
    x.selectedLimits["Hh"].limit().id() if "Hh" in x.selectedLimits else 0
    for x in df.hbResult
]
df["obsRHh"] = [
    x.selectedLimits["Hh"].obsRatio() if "Hh" in x.selectedLimits else 0
    for x in df.hbResult
]
df["selHp"] = [x.selectedLimits["Hp"].limit().id() for x in df.hbResult]
df["obsRHp"] = [x.selectedLimits["Hp"].obsRatio() for x in df.hbResult]

fig, axs = plt.subplots(ncols=3, sharex=True, sharey=True, figsize=(12, 4))
ax = axs[0]
cf = ax.tricontourf(
    df.mA,
    df.mHp,
    df.obsRHh,
    levels=np.arange(0, 1.01, 0.1),
    extend="max",
    cmap="Reds",
)
ax.set_title(r"$H$")

ax = axs[1]
ax.tricontourf(
    df.mA,
    df.mHp,
    df.obsRA,
    levels=np.arange(0, 1.01, 0.1),
    extend="max",
    cmap="Reds",
)
ax.set_title(r"$A$")

ax = axs[2]
ax.tricontourf(
    df.mA,
    df.mHp,
    df.obsRHp,
    levels=np.arange(0, 1.01, 0.1),
    extend="max",
    cmap="Reds",
)
ax.set_title(r"$H^\pm$")
fig.colorbar(cf, label="obsratio", ax=axs)

axs[0].set_ylabel("$m_{H^\pm}=m_H$ [GeV]")
for ax in axs:
    ax.set_xlabel("$m_A$ [GeV]")

In [ ]:
from matplotlib import patches as mpatches

relevantLimits = {
    h.id(): np.unique(df[df["obsR{}".format(h.id())] > 0.75]["sel{}".format(h.id())])
    for h in (hh, hA, Hp)
}

colors = {
    j: "C{}".format(i)
    for i, j in enumerate(np.unique(np.concatenate(list(relevantLimits.values()))))
}

fig, axs = plt.subplots(ncols=3, sharex=True, sharey=True, figsize=(12, 4))
for ax, h in zip(axs, (hh, hA, Hp)):
    ax.set_title({hh.id(): "$H$", hA.id(): "$A$", Hp.id(): "$H^\pm$"}[h.id()])
    for id in relevantLimits[h.id()]:
        cf = ax.tricontourf(
            df.mA,
            df.mHp,
            (df["sel{}".format(h.id())] == id).astype(int),
            levels=[0.5, 1.5],
            colors=colors[id],
        )
    ax.tricontour(
        df.mA, df.mHp, df["obsR{}".format(h.id())], levels=[1, 1e3], colors="k"
    )

patches = [mpatches.Patch(color=c) for j, c in colors.items()]
labels = [
    next(
        (
            "{} {} {}".format(x.experiment().name, x.reference(), x.processDesc())
            for x in bounds.limits()
            if x.id() == j
        )
    )
    for j, _ in colors.items()
]
axs[-1].legend(patches, labels, bbox_to_anchor=(0, 1), loc="upper left")
axs[0].set_ylabel("$m_{H^\pm}=m_H$ [GeV]")
for ax in axs:
    ax.set_xlabel("$m_A$ [GeV]")
plt.show()
